In [1]:
import pandas as pd
from scipy import stats
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
import glob
from functools import partial
from decimal import *


data='./3classdata/W/1.csv'
#data='./progetto/3classdata/Y/2.csv'
window=3
resolution=500
shift=3


In [2]:
def round(n):
    pst = '0.00001'
    precision = Decimal(pst)
    getcontext().prec = len(pst)
    return Decimal(n).quantize(precision)
assert round(5.00000000000000001)

In [3]:
def gaussian_interval(resolution):
    # use a gaussian distribution, mean 0, std deviation 0.25
    distribution = stats.norm(loc=0, scale=0.25)
    # bounds of range for inverse comulative distribution function
    bounds = distribution.cdf([-1, 1])
    # generate linear space of 2*resolution points using bounds
    linsp = np.linspace(*bounds, num=2*resolution)
    # obtain the array of 2*resolution points
    return distribution.ppf(linsp)
gaussian_interval(20)

array([-1.        , -0.48715223, -0.40806948, -0.3564728 , -0.31673373,
       -0.28370106, -0.25499594, -0.22931092, -0.20584419, -0.18406497,
       -0.16360107, -0.14417942, -0.1255919 , -0.10767457, -0.09029443,
       -0.07334053, -0.05671771, -0.04034218, -0.02413812, -0.00803494,
        0.00803494,  0.02413812,  0.04034218,  0.05671771,  0.07334053,
        0.09029443,  0.10767457,  0.1255919 ,  0.14417942,  0.16360107,
        0.18406497,  0.20584419,  0.22931092,  0.25499594,  0.28370106,
        0.31673373,  0.3564728 ,  0.40806948,  0.48715223,  1.        ])

In [4]:
df = pd.read_csv(data, dtype=float, header=None)
# rotate dataframe (each column is a temporal sequence)
df = df.T.reset_index().reindex(axis=1).drop(['index'], axis=1).infer_objects()


In [5]:
df = ((df - df.min()) / (df.max() - df.min()))*2 - 1
df.head()

0         1         2         3         4         5         6   \
0 -0.794245 -1.000000  0.828071 -0.994168  0.944798  0.668407 -0.373019   
1 -0.773646 -0.982051  0.838096 -1.000000  0.702760  0.490809 -0.536255   
2 -0.704494 -0.941707  0.867532 -0.971583  0.515924  0.189991 -0.667524   
3 -0.702488 -0.727678  0.847612 -0.956749  0.222930 -0.078956 -0.759538   
4 -0.653693 -0.474916  0.893637 -0.896301 -0.210191 -0.359162 -0.840516   

         7         8         9         10        11        12        13  \
0 -0.150670  0.847187  0.993011  0.997649  0.424828  0.707602 -0.548011   
1  0.522335  0.949622  1.000000  1.000000  0.416761  0.719298 -0.696552   
2  0.557023  0.946264  0.940591  0.540661 -0.131239  0.754386 -0.875862   
3  0.573242  0.914358  0.871396 -0.152875 -0.246231  0.766082 -0.839788   
4 -1.000000  0.993283  0.808842 -0.618419 -0.535811  0.812865 -0.818568   

         14        15        16        17        18        19  
0 -0.897720 -0.996191  0.733333  1.000000 -1.000000 -1.000000  
1 -0.840543 -1.000000  0.721212  0.707079 -0.989454 -0.998286  
2 -0.722166 -0.990737  0.715152  0.664768 -0.700204 -0.977304  
3 -0.739604 -0.937756  0.660606  0.243287 -0.358765 -0.947124  
4 -0.519115 -0.823284  0.630303  0.222132 -0.169913 -0.810559

In [6]:
#df = df.apply(partial(
   # discretize_series, gaussianInterval=gaussian_interval(resolution)))
#df.head()

In [7]:
l = df.apply(lambda x : pd.cut(x, gaussian_interval(resolution), right=True).apply(lambda l : l.left))
r = df.apply(lambda x : pd.cut(x, gaussian_interval(resolution), right=True).apply(lambda l : l.right))

In [8]:
df = l

In [9]:
 #df = df.round(5).astype(Decimal)
df.head()

0       1       2    3       4        5       6       7       8   \
0 -1.0000 -1.0000  0.7702 -1.0  0.7702  0.66230 -0.3744 -0.1507  0.7702   
1 -1.0000 -1.0000  0.7702 -1.0  0.6860  0.48980 -0.5422  0.5184  0.7702   
2 -0.7182 -1.0000  0.7702 -1.0  0.5132  0.18950 -0.6860  0.5562  0.7702   
3 -0.7182 -0.7702  0.7702 -1.0  0.2221 -0.07941 -0.7702  0.5722  0.7702   
4 -0.6623 -0.4775  0.7702 -1.0 -0.2102 -0.35970 -1.0000 -1.0000  0.7702   

       9       10      11      12      13      14   15      16      17  \
0  0.7702  0.7702  0.4237  0.6860 -0.5490 -1.0000 -1.0  0.7182  0.7702   
1  0.7702  0.7702  0.4159  0.7182 -0.7182 -1.0000 -1.0  0.7182  0.6860   
2  0.7702  0.5358 -0.1316  0.7182 -1.0000 -0.7702 -1.0  0.6860  0.6623   
3  0.7702 -0.1530 -0.2464  0.7182 -1.0000 -0.7702 -1.0  0.6433  0.2423   
4  0.7702 -0.6275 -0.5358  0.7702 -1.0000 -0.5240 -1.0  0.6275  0.2221   

       18   19  
0 -1.0000 -1.0  
1 -1.0000 -1.0  
2 -0.7182 -1.0  
3 -0.3597 -1.0  
4 -0.1700 -1.0

In [10]:
def generate_words(col, w, s):
    word = []
    idx = 0
    distance = abs(w-s)
    while idx < len(col):
        if len(word) == w:
            yield tuple(word)
            word = []
            if w < s and idx == w:
                idx += distance
            if w > s:
                idx -= distance 
        else:
            word.append(round(col[idx]))
            idx+=1

In [11]:
def rolling_window(df, w, s):
    ret = list()
    for _,col in df.iteritems():
        ret.append(tuple(generate_words(col, w, s)))
    return pd.DataFrame(ret).T.reset_index().reindex(axis=1).drop(['index'], axis=1)

In [12]:
rol = rolling_window(df, 5, 3)
print(rol)
print(type(rol))

                                                   0   \
0   (-1.00000, -1.00000, -0.71820, -0.71820, -0.66...   
1   (-0.71820, -0.66230, -0.28860, -0.12660, 0.16140)   
2      (-0.12660, 0.16140, 0.49410, 0.50810, 0.60180)   
3       (0.50810, 0.60180, 0.66230, 0.77020, 0.77020)   
4       (0.77020, 0.77020, 0.77020, 0.77020, 0.77020)   
5       (0.77020, 0.77020, 0.77020, 0.77020, 0.77020)   
6       (0.77020, 0.77020, 0.77020, 0.77020, 0.77020)   
7       (0.77020, 0.77020, 0.77020, 0.77020, 0.66230)   
8      (0.77020, 0.66230, 0.26220, 0.24640, -0.22390)   
9   (0.24640, -0.22390, -0.34940, -0.77020, -1.00000)   
10  (-0.77020, -1.00000, -1.00000, -1.00000, -1.00...   
11  (-1.00000, -1.00000, -1.00000, -1.00000, -1.00...   

                                                   1   \
0   (-1.00000, -1.00000, -1.00000, -0.77020, -0.47...   
1   (-0.77020, -0.47750, -0.71820, -0.37440, -0.04...   
2     (-0.37440, -0.04573, 0.24950, 0.54220, 0.44340)   
3       (0.54220, 0.44340, 0.3

In [13]:
def text_freq(iterable):
    d = dict()
    for df in iterable:
        assert type(df) is pd.DataFrame, 'Wrong type:' + str(type(df))
        for _,col in df.iteritems():
            for word, cnt in col.value_counts().iteritems():
                hashable = word # hashable to be used as index
                if hashable in d:
                    d[hashable] += cnt
                else:
                    d[hashable] = cnt
        return d

text_freq((rol,))

{(Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-1.00000')): 23,
 (Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-0.77020')): 2,
 (Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-0.77020'),
  Decimal('-0.47750')): 1,
 (Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-0.66230'),
  Decimal('-0.47750')): 1,
 (Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-0.38230'),
  Decimal('-0.19620')): 1,
 (Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-0.34290'),
  Decimal('0.19200')): 1,
 (Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-0.77020'),
  Decimal('-1.00000'),
  Decimal('-0.77020')): 1,
 (Decimal('-1.00000'),
  Decimal('-1.00000'),
  Decimal('-0.77020'),
  Decimal('-0.77020'),
  Decimal('-0.77020')): 1,
 (Decimal('-1.00000'),
  Decimal('-1.00000'),
  